# Tie Rod Force Analysis

### Overview

This data was collected during a test day on [insert test day here]. The main purpose of the test was to observe the forces exerted on the tie rod during aggressive turns. The tie rod is a critical component in the steering mechanism, and understanding the forces it experiences is essential for ensuring the safety and performance of the vehicle.

### Data Collection

The data was collected using strain gauges attached to the tie rod. The strain gauges measure the deformation of the tie rod, which can be used to calculate the forces acting on it. The data was recorded at 100 Hz to capture the dynamic behavior of the tie rod during aggressive maneuvers.

### Data Analysis

The following sections provide a detailed analysis of the collected data. Each cell in the analysis is explained in detail, including the mathematical operations performed and the significance of the visualizations.


In [230]:
from scipy.signal import find_peaks
import pandas as pd
import numpy as np
# Remove matplotlib import and use Plotly instead
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Load and Clean Data

The `load_and_clean_data` function reads the data from a CSV file and cleans it by removing rows with invalid values. It also adds a `Time` column to the DataFrame to represent the time index of each data point.

## Data Cleaning and Preparation

In this section, we define a function `load_and_clean_data` that is responsible for loading the raw data from a CSV file and performing necessary cleaning operations. The function reads the data into a pandas DataFrame and adds a `Time` column to represent the time index of each data point.

The data cleaning process involves filtering the DataFrame to remove rows with invalid or irrelevant values. Specifically, we:
- Remove rows where the engine speed (`S8 RPM`) is below 2000, as these data points are not relevant for our analysis.
- Remove rows where the absolute value of inline acceleration (`InlineAcc`) is less than 0.2, as these data points indicate low dynamic activity.
- Remove statistical outliers in the `TieRodForce` column by excluding values that are more than three standard deviations away from the mean.

The cleaned DataFrame, `moving_df`, is then returned for further analysis. This step ensures that the data we analyze is relevant and free from noise, improving the accuracy and reliability of our subsequent analyses.

In [231]:
def load_and_clean_data(file_path):
    df = pd.read_csv(file_path)

    df['Time'] = np.arange(0, len(df) * 0.01, 0.01)

    moving_df = df[
        (df['S8 RPM'] > 2000) &
        (df['InlineAcc'].abs() > 0.2) &
        (df['TieRodForce'].abs() < df['TieRodForce'].std() * 3)  # Remove statistical outliers
        ].copy()
    return moving_df

## Analyze Tie Rod Forces

The `analyze_tie_rod_forces` function is designed to provide a comprehensive analysis of the tie rod forces, which is essential for several reasons:

> - **Safety and Performance**: Understanding the forces acting on the tie rod is crucial for ensuring the safety and performance of the vehicle. By identifying the maximum and minimum forces, we can assess whether the tie rod is operating within safe limits.
> - **Correlation Analysis**: The correlation coefficient helps in understanding how closely the tie rod forces are related to lateral acceleration. A strong correlation indicates that lateral acceleration is a significant factor influencing tie rod forces.
> - **Event Context**: By examining the context around extreme force events, we can gain insights into the driving conditions and maneuvers that lead to these peaks. This information is valuable for improving vehicle design and driving strategies.
> - **Trend Visualization**: The regression line provides a clear visualization of the relationship between tie rod forces and lateral acceleration, making it easier to interpret the data and identify trends.

1. **Correlation Calculation**: 
    - The function calculates the correlation coefficient between the tie rod forces (`TieRodForce`) and lateral acceleration (`LateralAcc`). This coefficient quantifies the strength and direction of the linear relationship between these two variables.

2. **Maximum and Minimum Force Events**:
    - The function identifies the maximum and minimum tie rod force values in the dataset. These extreme values are critical for understanding the peak loads experienced by the tie rod.
    - It also extracts the context around these events by selecting a window of data points (10 points before and after the event) to provide a detailed view of the conditions leading up to and following these extreme forces.

3. **Regression Line Calculation**:
    - The function calculates the slope and intercept of the regression line that best fits the relationship between tie rod forces and lateral acceleration. This regression line helps in visualizing the trend and making predictions based on the observed data.

Overall, this function is a key component of our data analysis workflow, providing valuable insights into the behavior of the tie rod under different driving conditions.


In [232]:
def analyze_tie_rod_forces(df, context_length=10):
    correlation = df['TieRodForce'].corr(df['LateralAcc'])

    max_force = df['TieRodForce'].max()
    min_force = df['TieRodForce'].min()

    max_idx = df['TieRodForce'].idxmax()
    min_idx = df['TieRodForce'].idxmin()

    max_context = df.loc[max_idx-context_length:max_idx+context_length,
                  ['Time', 'TieRodForce', 'LateralAcc', 'InlineAcc', 'S8 RPM']]
    min_context = df.loc[min_idx-context_length:min_idx+context_length,
                  ['Time', 'TieRodForce', 'LateralAcc', 'InlineAcc', 'S8 RPM']]

    slope, intercept = np.polyfit(df['LateralAcc'], df['TieRodForce'], 1)

    return {
        'correlation': correlation,
        'max_force': max_force,
        'min_force': min_force,
        'max_context': max_context,
        'min_context': min_context,
        'regression': {'slope': slope, 'intercept': intercept}
        }

## Plot Force Analysis

The `force_analysis` function visualizes the maximum and minimum tie rod force events along with the corresponding lateral acceleration values.

1. **Maximum Force Event Analysis**:
    - The function first plots the tie rod force over time for the maximum force event. This helps in understanding the behavior of the tie rod during the peak force event.
    - A twin axis is used to plot the lateral acceleration on the same graph, allowing for a direct comparison between the tie rod force and lateral acceleration.

2. **Minimum Force Event Analysis**:
    - Similarly, the function plots the tie rod force over time for the minimum force event. This helps in understanding the behavior of the tie rod during the lowest force event.
    - A twin axis is used to plot the lateral acceleration on the same graph, allowing for a direct comparison between the tie rod force and lateral acceleration.

Overall, this function provides a comprehensive visualization of the tie rod force events, allowing for a detailed analysis of the conditions leading up to and following the peak force events. This information is valuable for understanding the dynamic behavior of the tie rod and its interaction with lateral acceleration during aggressive maneuvers.

In [233]:
def force_analysis(max_context, min_context):


    # Debug prints to verify the data
    print("Max Context Data:")
    print(max_context[['Time', 'TieRodForce', 'LateralAcc']].head())
    print("Min Context Data:")
    print(min_context[['Time', 'TieRodForce', 'LateralAcc']].head())

    # Maximum Force Event Analysis
    max_fig = go.Figure()

    max_fig.add_trace(go.Scatter(
        x=max_context['Time'],
        y=max_context['TieRodForce'],
        mode='lines+markers',
        name='Tie Rod Force',
        line=dict(color='blue')
    ))

    max_fig.add_trace(go.Scatter(
        x=max_context['Time'],
        y=max_context['LateralAcc'],
        mode='lines',
        name='Lateral Acceleration',
        line=dict(color='red', dash='dash'),
        yaxis='y2'
    ))

    max_val = max_context['TieRodForce'].max()
    max_time = max_context.loc[max_context['TieRodForce'].idxmax(), 'Time']
    max_fig.add_annotation(
        x=max_time,
        y=max_val,
        text=f"Max: {max_val:.2f} N",
        showarrow=True,
        arrowhead=2
    )

    max_fig.update_layout(
        title='Maximum Force Event Analysis',
        xaxis_title='Time (s)',
        yaxis=dict(
            title='Force (N)',
            titlefont=dict(color='blue'),
            tickfont=dict(color='blue')
        ),
        yaxis2=dict(
            title='Lateral Acceleration (g)',
            titlefont=dict(color='red'),
            tickfont=dict(color='red'),
            overlaying='y',
            side='right'
        ),
        template="plotly_dark"
    )

    # Minimum Force Event Analysis
    min_fig = go.Figure()

    min_fig.add_trace(go.Scatter(
        x=min_context['Time'],
        y=min_context['TieRodForce'],
        mode='lines+markers',
        name='Tie Rod Force',
        line=dict(color='blue')
    ))

    min_fig.add_trace(go.Scatter(
        x=min_context['Time'],
        y=min_context['LateralAcc'],
        mode='lines',
        name='Lateral Acceleration',
        line=dict(color='red', dash='dash'),
        yaxis='y2'
    ))

    min_val = min_context['TieRodForce'].min()
    min_time = min_context.loc[min_context['TieRodForce'].idxmin(), 'Time']
    min_fig.add_annotation(
        x=min_time,
        y=min_val,
        text=f"Min: {min_val:.2f} N",
        showarrow=True,
        arrowhead=2
    )

    min_fig.update_layout(
        title='Minimum Force Event Analysis',
        xaxis_title='Time (s)',
        yaxis=dict(
            title='Force (N)',
            titlefont=dict(color='blue'),
            tickfont=dict(color='blue')
        ),
        yaxis2=dict(
            title='Lateral Acceleration (g)',
            titlefont=dict(color='red'),
            tickfont=dict(color='red'),
            overlaying='y',
            side='right'
        ),
        template="plotly_dark"
    )

    max_fig.show()
    min_fig.show()

    return max_fig, min_fig

## Histogram of Tie Rod Forces

The `force_histogram` function is designed to provide a visual representation of the distribution of absolute tie rod forces in the dataset. This histogram helps in understanding the frequency and magnitude of forces experienced by the tie rod during the test.

1. **Visualization of Force Distribution**:
    - The histogram provides a clear visual representation of how often different magnitudes of tie rod forces occur. This is crucial for identifying common force ranges and understanding the overall behavior of the tie rod under various conditions.

2. **Mean and Median Values**:
    - By displaying the mean and median values on the histogram, we can quickly assess the central tendency of the tie rod forces. The mean gives an average value, while the median provides the middle value, which is less affected by outliers. These metrics are important for summarizing the data and identifying typical force levels.

Overall, this function is a key component of the data analysis workflow, providing valuable insights into the distribution and central tendency of tie rod forces. Understanding these aspects is essential for assessing the performance and safety of the tie rod under different driving conditions.

In [234]:
def force_histogram(df):
    abs_forces = df['TieRodForce'].abs()
    max_force = abs_forces.max()
    fig = go.Figure()
    fig.add_trace(go.Histogram(
        x=abs_forces,
        xbins=dict(start=0, end=max_force+10, size=10),
        marker_color='#00ffff',
        opacity=0.7
    ))
    mean_force = abs_forces.mean()
    median_force = abs_forces.median()
    fig.add_vline(x=mean_force, line=dict(color='#ff4444', dash='dash'),
                  annotation_text=f"Mean: {mean_force:.2f}")
    fig.add_vline(x=median_force, line=dict(color='#44ff44', dash='dash'),
                  annotation_text=f"Median: {median_force:.2f}")
    fig.update_layout(
        title="Distribution of Absolute Tie Rod Forces",
        xaxis_title="Absolute Tie Rod Force",
        yaxis_title="Frequency",
        template="plotly_dark"
    )
    fig.show()

## High Force Histogram

The `high_force_histogram` function creates a histogram of the absolute tie rod forces above 200. It also displays the mean and median values of the tie rod forces above the threshold.

1. **Filtering High Forces**:
    - The function filters the dataset to include only the data points where the absolute value of the tie rod force is greater than 200. This ensures that the histogram focuses on the most significant force events, which are likely to have the greatest impact on the tie rod's performance and durability.

2. **Visualization of High Force Distribution**:
    - The histogram provides a clear visual representation of the distribution of high tie rod forces. This helps in identifying the frequency and magnitude of these extreme forces, which is essential for assessing the tie rod's ability to withstand high loads.

3. **Mean and Median Values**:
    - By displaying the mean and median values on the histogram, we can quickly assess the central tendency of the high tie rod forces. The mean gives an average value, while the median provides the middle value, which is less affected by outliers. These metrics are important for summarizing the data and identifying typical force levels under high-stress conditions.

Overall, this function is a key component of the data analysis workflow, providing valuable insights into the distribution and central tendency of high tie rod forces. Understanding these aspects is essential for assessing the performance and safety of the tie rod under extreme driving conditions.

In [235]:
def high_force_histogram(df):
    abs_forces = df.loc[df['TieRodForce'].abs() > 200, 'TieRodForce'].abs()
    max_force = abs_forces.max()
    fig = go.Figure()
    fig.add_trace(go.Histogram(
        x=abs_forces,
        xbins=dict(start=200, end=max_force+10, size=10),
        marker_color='#00ffff',
        opacity=0.7
    ))
    mean_force = abs_forces.mean()
    median_force = abs_forces.median()
    fig.add_vline(x=mean_force, line=dict(color='#ff4444', dash='dash'),
                  annotation_text=f"Mean: {mean_force:.2f}")
    fig.add_vline(x=median_force, line=dict(color='#44ff44', dash='dash'),
                  annotation_text=f"Median: {median_force:.2f}")
    fig.update_layout(
        title="Distribution of Absolute Tie Rod Forces Above 200",
        xaxis_title="Absolute Tie Rod Force (N)",
        yaxis_title="Frequency",
        template="plotly_dark"
    )
    fig.show()

## Correlation Plot

The `correlation_plot` function creates a scatter plot of tie rod forces against lateral acceleration. It also overlays a regression line that best fits the data points and displays the correlation coefficient between the two variables.

**Scatter Plot of Data Points**:
    The function begins by creating a scatter plot of the tie rod forces (`TieRodForce`) against lateral acceleration (`LateralAcc`). Each point on the scatter plot represents a single data point from the dataset. This visualization helps in identifying the overall distribution and spread of the data.


In [236]:
def correlation_plot(df, correlation, regression):
    fig = go.Figure()
    fig.add_trace(go.Scatter(
        x=df['LateralAcc'], y=df['TieRodForce'],
        mode='markers', marker=dict(color='blue', opacity=0.1),
        name='Data Points'
    ))
    x_vals = np.array([df['LateralAcc'].min(), df['LateralAcc'].max()])
    y_vals = regression['slope'] * x_vals + regression['intercept']
    fig.add_trace(go.Scatter(
        x=x_vals, y=y_vals,
        mode='lines', line=dict(color='red', dash='dash'),
        name=f"Trend Line: y = {regression['slope']:.2f}x + {regression['intercept']:.2f}"
    ))
    fig.add_annotation(
        x=0.05, y=0.95, xref="paper", yref="paper",
        text=f"Correlation Coefficient: {correlation:.4f}",
        showarrow=False, font=dict(size=12)
    )
    fig.update_layout(
        title="Tie Rod Force vs Lateral Acceleration",
        xaxis_title="Lateral Acceleration",
        yaxis_title="Tie Rod Force"
    )
    fig.show()

## Absolute Forces

The `absolute_forces` function calculates the absolute values of the tie rod forces and lateral acceleration and plots them on the same graph. By plotting these absolute values on the same graph, we can directly compare the magnitudes of the forces and accelerations, regardless of their direction.

1. **Calculation of Absolute Values**:
    - The function begins by calculating the absolute values of the tie rod forces (`AbsTieRodForce`) and lateral acceleration (`AbsLateralAcc`). This is done to ensure that we are only considering the magnitude of these values, which is important for understanding the overall stress and strain on the tie rod, irrespective of the direction of the forces and accelerations.

2. **Visualization**:
    - The function then creates a plot with two lines: one representing the absolute tie rod forces and the other representing the absolute lateral acceleration. By plotting these values on the same graph, we can easily compare their magnitudes and observe any correlations or patterns between them.
    - The x-axis represents the index of the data points, while the y-axis represents the absolute values of the tie rod forces and lateral acceleration. This visualization helps in identifying periods of high stress and acceleration, which are critical for understanding the dynamic behavior of the tie rod during aggressive maneuvers.

Overall, this function provides a valuable visualization that helps in understanding the relationship between tie rod forces and lateral acceleration, and it is an essential step in our data analysis workflow.

In [237]:
def absolute_forces(df):
    df['AbsTieRodForce'] = df['TieRodForce'].abs()
    df['AbsLateralAcc'] = df['LateralAcc'].abs()
    fig = go.Figure()
    fig.add_trace(go.Scatter(
        x=df.index, y=df['AbsTieRodForce'],
        mode='lines', name='Absolute Tie Rod Force', line=dict(color='blue')
    ))
    fig.add_trace(go.Scatter(
        x=df.index, y=df['AbsLateralAcc'],
        mode='lines', name='Absolute Lateral Acceleration', line=dict(color='red')
    ))
    fig.update_layout(
        title="Absolute Tie Rod Force vs Absolute Lateral Acceleration",
        xaxis_title="Index", yaxis_title="Absolute Values"
    )
    fig.show()

## Average Peaks

The `average_peaks` function identifies the peaks in the tie rod force and lateral acceleration data and calculates the average values of these peaks.

The `average_peaks` function is designed to identify significant peaks in the tie rod force and lateral acceleration data. This is achieved using the `find_peaks` function from the `scipy.signal` module, which detects local maxima in the data based on specified height thresholds.

1. **Identifying Tie Rod Force Peaks**:
    - The function first identifies peaks in the absolute tie rod force data (`AbsTieRodForce`) that are greater than 120 N. This threshold is chosen to focus on significant force events that are likely to impact the tie rod's performance and durability.
    - The indices of these peaks are stored in the `tie_rod_peaks` array, and the corresponding peak values are extracted into the `tie_rod_peak_values` series.

2. **Identifying Lateral Acceleration Peaks**:
    - Similarly, the function identifies peaks in the absolute lateral acceleration data (`AbsLateralAcc`) that are greater than 0.5 g. This threshold is chosen to focus on significant acceleration events that are likely to influence the tie rod forces.
    - The indices of these peaks are stored in the `lateral_acc_peaks` array, and the corresponding peak values are extracted into the `lateral_acc_peak_values` series.

3. **Calculating Average Peak Values**:
    - The function calculates the average value of the identified tie rod force peaks (`avg_tie_rod_peaks`) and the average value of the identified lateral acceleration peaks (`avg_lateral_acc_peaks`). These averages provide a summary measure of the typical peak values in the dataset, which is useful for understanding the overall behavior of the tie rod and its response to lateral acceleration.

By identifying and averaging the peaks in the tie rod force and lateral acceleration data, this function provides valuable insights into the extreme conditions experienced by the tie rod during aggressive maneuvers. This information is crucial for assessing the performance and safety of the tie rod under high-stress conditions.

In [238]:
def average_peaks(df):
    df['AbsTieRodForce'] = df['TieRodForce'].abs()
    df['AbsLateralAcc'] = df['LateralAcc'].abs()
    tie_rod_peaks, _ = find_peaks(df['AbsTieRodForce'], height=120)
    tie_rod_peak_values = df['AbsTieRodForce'].iloc[tie_rod_peaks]

    lateral_acc_peaks, _ = find_peaks(df['AbsLateralAcc'], height=0.5)
    lateral_acc_peak_values = df['AbsLateralAcc'].iloc[lateral_acc_peaks]

    avg_tie_rod_peaks = tie_rod_peak_values.mean()
    avg_lateral_acc_peaks = lateral_acc_peak_values.mean()

    print(f"Average Tie Rod Force Peak: {avg_tie_rod_peaks:.2f}")
    print(f"Average Lateral Acceleration Peak: {avg_lateral_acc_peaks:.2f} ")

## Main Function

The `main` function loads the data, analyzes the tie rod forces, and generates visualizations to provide insights into the data.It performs the following key steps:

1. **Loading and Cleaning Data**:
    - The function begins by calling `load_and_clean_data` to read the data from the CSV file `tie_rod.csv` and perform necessary cleaning operations. This ensures that the data used for analysis is relevant and free from noise, improving the accuracy and reliability of the subsequent analyses.

2. **Analyzing Tie Rod Forces**:
    - The `analyze_tie_rod_forces` function is called to calculate the correlation between tie rod forces and lateral acceleration, identify maximum and minimum force events, and compute the regression line. This analysis provides valuable insights into the behavior of the tie rod under different driving conditions.

3. **Visualizing Absolute Forces**:
    - The `absolute_forces` function is called to calculate and plot the absolute values of tie rod forces and lateral acceleration. This visualization helps in understanding the overall stress and strain on the tie rod, irrespective of the direction of the forces and accelerations.

4. **Identifying and Averaging Peaks**:
    - The `average_peaks` function identifies significant peaks in the tie rod force and lateral acceleration data and calculates the average values of these peaks. This information is crucial for assessing the performance and safety of the tie rod under high-stress conditions.

5. **Printing Summary Statistics**:
    - The function prints the number of valid data points, the correlation coefficient, and the maximum and minimum tie rod forces. These summary statistics provide a quick overview of the key findings from the analysis.

6. **Force Event Analysis**:
    - The `force_analysis` function is called to visualize the maximum and minimum tie rod force events along with the corresponding lateral acceleration values. This detailed analysis helps in understanding the conditions leading up to and following the peak force events.

7. **Correlation Plot**:
    - The `correlation_plot` function creates a scatter plot of tie rod forces against lateral acceleration and overlays a regression line. This visualization helps in identifying the overall trend and making predictions based on the observed data.

8. **Force Histograms**:
    - The `force_histogram` function creates a histogram of the absolute tie rod forces to visualize the distribution of forces in the dataset.
    - The `high_force_histogram` function creates a histogram of the absolute tie rod forces above 200 to focus on the most significant force events.

By executing these steps, the `main` function provides a comprehensive analysis of the tie rod forces, offering valuable insights into the dynamic behavior of the tie rod during aggressive maneuvers. This information is essential for ensuring the safety and performance of the vehicle.

In [239]:
def main():
    df = load_and_clean_data('tie_rod.csv')

    df_normal = pd.read_csv('tie_rod.csv')

    print("Columns in df_normal:", df_normal.columns)

    results = analyze_tie_rod_forces(df, 10)

    absolute_forces(df_normal)

    average_peaks(df)

    print(f"Number of valid data points: {len(df)}")
    print(f"Correlation coefficient: {results['correlation']:.4f}")
    print(f"Maximum tie rod force: {results['max_force']:.2f}")
    print(f"Minimum tie rod force: {results['min_force']:.2f}")

    fig1, fig2 = force_analysis(results['max_context'], results['min_context'])
    fig3 = correlation_plot(df, results['correlation'], results['regression'])
    fig4 = force_histogram(df_normal)
    fig5 = high_force_histogram(df_normal)


if __name__ == "__main__":
    main()

Columns in df_normal: Index(['Time', 'Logger Temperature', 'External Voltage', 'InlineAcc',
       'LateralAcc', 'VerticalAcc', 'RollRate', 'PitchRate', 'YawRate',
       'RBrakePressCorr', 'FBrakePressCorr', 'Brake Bias', 'TieRodForce',
       'S8 RPM', 'S8 radarSpeed', 'S8 dSPEED', 'S8 wheelSpin', 'S8 rfspeed',
       'S8 lfSpeed', 'S8 lrSpeed', 'S8 rrSpeed', 'S8 lam1', 'S8 ft1', 'S8 eot',
       'S8 act1', 'S8 ft1V', 'S8 ect1', 'S8 eop', 'S8 fp1', 'S8 map1',
       'S8 vbat', 'S8 gearCutState', 'S8 gear', 'S8 gearShiftDeci',
       'S8 paddleSwitch', 'S8 gearDownOut', 'runMode', 'S8 neutHalfShift',
       'S8 neutShiftSEV', 'fuelConsVolLR', 'S8 fuelDutyPri1', 'S8 fuelBase1',
       'S8 fuelFinalPri1', 'S8 fuelEndAngle', 'S8 fuelMltOrfcEn',
       'S8 fuelConsMass', 'S8 fuelConVolRat', 'S8 ignBase1', 'S8 ignFinal1',
       'S8 tps1', 'S8 tpsClosed', 'S8 tpsLow', 'S8 tfcSum1', 'S8 swa',
       'S8 tfcAdd1', 'S8 calSwitchV', 'S8 engineEnable', 'S8 calSelect',
       'S8 LaunchSwitch', 

Average Tie Rod Force Peak: 131.95
Average Lateral Acceleration Peak: 1.14 
Number of valid data points: 15917
Correlation coefficient: 0.6047
Maximum tie rod force: 143.39
Minimum tie rod force: -143.35
Max Context Data:
         Time  TieRodForce  LateralAcc
11476  114.76      113.776        0.88
11477  114.77      131.500        0.86
11478  114.78      131.500        0.77
11479  114.79      131.068        0.91
11480  114.80      129.820        1.00
Min Context Data:
         Time  TieRodForce  LateralAcc
45837  458.37     -126.800       -1.16
45840  458.40     -137.168       -0.85
45845  458.45     -104.180       -1.05
45846  458.46     -130.100       -1.16
45847  458.47     -143.348       -1.32
